# Clustering Crypto

In [2]:
# Initial imports
import pandas as pd
import hvplot.pandas
from path import Path
import plotly.express as px
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans

### Deliverable 1: Preprocessing the Data for PCA

In [58]:
# Load the crypto_data.csv dataset.
file_path = "Resources/crypto_data.csv"
cc_df = pd.read_csv(file_path)
cc_df

Unnamed: 0        CoinName Algorithm  IsTrading ProofType  \
0            42         42 Coin    Scrypt       True   PoW/PoS   
1           365         365Coin       X11       True   PoW/PoS   
2           404         404Coin    Scrypt       True   PoW/PoS   
3           611       SixEleven   SHA-256       True       PoW   
4           808             808   SHA-256       True   PoW/PoS   
...         ...             ...       ...        ...       ...   
1247        XBC     BitcoinPlus    Scrypt       True       PoS   
1248       DVTC      DivotyCoin    Scrypt      False   PoW/PoS   
1249       GIOT     Giotto Coin    Scrypt      False   PoW/PoS   
1250       OPSC  OpenSourceCoin   SHA-256      False   PoW/PoS   
1251       PUNK       SteamPunk       PoS      False       PoS   

      TotalCoinsMined TotalCoinSupply  
0        4.199995e+01              42  
1                 NaN      2300000000  
2        1.055185e+09       532000000  
3                 NaN          611000  
4        0.000000e+00               0  
...               ...             ...  
1247     1.283270e+05         1000000  
1248     2.149121e+07       100000000  
1249              NaN       233100000  
1250              NaN        21000000  
1251              NaN        40000000  

[1252 rows x 7 columns]

In [4]:
# Keep all the cryptocurrencies that are being traded.
indexNames = cc_df[ cc_df['IsTrading'] == False ].index
indexNames
cc_df.drop(indexNames , inplace=True)
print(f"Duplicate entries: {cc_df.duplicated().sum()}")

Duplicate entries: 0


In [5]:
# Remove the "IsTrading" column. 
cc_df.drop(columns=["IsTrading"], inplace=True)
cc_df.head()

Unnamed: 0   CoinName Algorithm ProofType  TotalCoinsMined TotalCoinSupply
0         42    42 Coin    Scrypt   PoW/PoS     4.199995e+01              42
1        365    365Coin       X11   PoW/PoS              NaN      2300000000
2        404    404Coin    Scrypt   PoW/PoS     1.055185e+09       532000000
3        611  SixEleven   SHA-256       PoW              NaN          611000
4        808        808   SHA-256   PoW/PoS     0.000000e+00               0

In [6]:
# Remove rows that have at least 1 null value.
cc_df = cc_df.dropna()
for column in cc_df.columns:
    print(f"Column {column} has {cc_df[column].isnull().sum()} null values")

Column Unnamed: 0 has 0 null values
Column CoinName has 0 null values
Column Algorithm has 0 null values
Column ProofType has 0 null values
Column TotalCoinsMined has 0 null values
Column TotalCoinSupply has 0 null values


In [7]:
# Check the look of the DataFrame
cc_df

Unnamed: 0     CoinName    Algorithm ProofType  TotalCoinsMined  \
0            42      42 Coin       Scrypt   PoW/PoS     4.199995e+01   
2           404      404Coin       Scrypt   PoW/PoS     1.055185e+09   
4           808          808      SHA-256   PoW/PoS     0.000000e+00   
5          1337    EliteCoin          X13   PoW/PoS     2.927942e+10   
7           BTC      Bitcoin      SHA-256       PoW     1.792718e+07   
...         ...          ...          ...       ...              ...   
1238       ZEPH       ZEPHYR      SHA-256      DPoS     2.000000e+09   
1242        GAP      Gapcoin       Scrypt   PoW/PoS     1.493105e+07   
1245        BDX       Beldex  CryptoNight       PoW     9.802226e+08   
1246        ZEN      Horizen     Equihash       PoW     7.296538e+06   
1247        XBC  BitcoinPlus       Scrypt       PoS     1.283270e+05   

     TotalCoinSupply  
0                 42  
2          532000000  
4                  0  
5       314159265359  
7           21000000  
...              ...  
1238      2000000000  
1242       250000000  
1245      1400222610  
1246        21000000  
1247         1000000  

[685 rows x 6 columns]

In [8]:
# Keep all the cryptocurrencies that have a working algorithm.
workingAlgorithm = cc_df[ cc_df['TotalCoinsMined'] == 0 ].index
workingAlgorithm
cc_df.drop(workingAlgorithm , inplace=True)
cc_df

Unnamed: 0     CoinName    Algorithm ProofType  TotalCoinsMined  \
0            42      42 Coin       Scrypt   PoW/PoS     4.199995e+01   
2           404      404Coin       Scrypt   PoW/PoS     1.055185e+09   
5          1337    EliteCoin          X13   PoW/PoS     2.927942e+10   
7           BTC      Bitcoin      SHA-256       PoW     1.792718e+07   
8           ETH     Ethereum       Ethash       PoW     1.076842e+08   
...         ...          ...          ...       ...              ...   
1238       ZEPH       ZEPHYR      SHA-256      DPoS     2.000000e+09   
1242        GAP      Gapcoin       Scrypt   PoW/PoS     1.493105e+07   
1245        BDX       Beldex  CryptoNight       PoW     9.802226e+08   
1246        ZEN      Horizen     Equihash       PoW     7.296538e+06   
1247        XBC  BitcoinPlus       Scrypt       PoS     1.283270e+05   

     TotalCoinSupply  
0                 42  
2          532000000  
5       314159265359  
7           21000000  
8                  0  
...              ...  
1238      2000000000  
1242       250000000  
1245      1400222610  
1246        21000000  
1247         1000000  

[533 rows x 6 columns]

In [21]:
# Change index for new dataframe
cleaned_crypto_df = cc_df.set_index('Unnamed: 0')
cleaned_crypto_df.index.name = None
cleaned_crypto_df

CoinName    Algorithm ProofType  TotalCoinsMined TotalCoinSupply
42        42 Coin       Scrypt   PoW/PoS     4.199995e+01              42
404       404Coin       Scrypt   PoW/PoS     1.055185e+09       532000000
1337    EliteCoin          X13   PoW/PoS     2.927942e+10    314159265359
BTC       Bitcoin      SHA-256       PoW     1.792718e+07        21000000
ETH      Ethereum       Ethash       PoW     1.076842e+08               0
...           ...          ...       ...              ...             ...
ZEPH       ZEPHYR      SHA-256      DPoS     2.000000e+09      2000000000
GAP       Gapcoin       Scrypt   PoW/PoS     1.493105e+07       250000000
BDX        Beldex  CryptoNight       PoW     9.802226e+08      1400222610
ZEN       Horizen     Equihash       PoW     7.296538e+06        21000000
XBC   BitcoinPlus       Scrypt       PoS     1.283270e+05         1000000

[533 rows x 5 columns]

In [10]:
# Create a new DataFrame that holds only the cryptocurrencies names.
coinNames = cleaned_crypto_df.loc[:, ['CoinName']]
coinNames

CoinName
42        42 Coin
404       404Coin
1337    EliteCoin
BTC       Bitcoin
ETH      Ethereum
...           ...
ZEPH       ZEPHYR
GAP       Gapcoin
BDX        Beldex
ZEN       Horizen
XBC   BitcoinPlus

[533 rows x 1 columns]

In [11]:
# Drop the 'CoinName' column since it's not going to be used on the clustering algorithm.
cleaned_crypto_df.drop(columns=["CoinName"], inplace=True)
cleaned_crypto_df.head()

Algorithm ProofType  TotalCoinsMined TotalCoinSupply
42      Scrypt   PoW/PoS     4.199995e+01              42
404     Scrypt   PoW/PoS     1.055185e+09       532000000
1337       X13   PoW/PoS     2.927942e+10    314159265359
BTC    SHA-256       PoW     1.792718e+07        21000000
ETH     Ethash       PoW     1.076842e+08               0

In [12]:
# Use get_dummies() to create variables for text features.
x = pd.get_dummies(cleaned_crypto_df, columns=['Algorithm', 'ProofType'], drop_first=True)
x

TotalCoinsMined TotalCoinSupply  Algorithm_536  Algorithm_Argon2d  \
42       4.199995e+01              42              0                  0   
404      1.055185e+09       532000000              0                  0   
1337     2.927942e+10    314159265359              0                  0   
BTC      1.792718e+07        21000000              0                  0   
ETH      1.076842e+08               0              0                  0   
...               ...             ...            ...                ...   
ZEPH     2.000000e+09      2000000000              0                  0   
GAP      1.493105e+07       250000000              0                  0   
BDX      9.802226e+08      1400222610              0                  0   
ZEN      7.296538e+06        21000000              0                  0   
XBC      1.283270e+05         1000000              0                  0   

      Algorithm_BLAKE256  Algorithm_Blake  Algorithm_Blake2S  \
42                     0                0                  0   
404                    0                0                  0   
1337                   0                0                  0   
BTC                    0                0                  0   
ETH                    0                0                  0   
...                  ...              ...                ...   
ZEPH                   0                0                  0   
GAP                    0                0                  0   
BDX                    0                0                  0   
ZEN                    0                0                  0   
XBC                    0                0                  0   

      Algorithm_Blake2b  Algorithm_C11  Algorithm_Cloverhash  ...  \
42                    0              0                     0  ...   
404                   0              0                     0  ...   
1337                  0              0                     0  ...   
BTC                   0              0                     0  ...   
ETH                   0              0                     0  ...   
...                 ...            ...                   ...  ...   
ZEPH                  0              0                     0  ...   
GAP                   0              0                     0  ...   
BDX                   0              0                     0  ...   
ZEN                   0              0                     0  ...   
XBC                   0              0                     0  ...   

      ProofType_PoW/PoS  ProofType_PoW/PoS   ProofType_PoW/PoW  \
42                    1                   0                  0   
404                   1                   0                  0   
1337                  1                   0                  0   
BTC                   0                   0                  0   
ETH                   0                   0                  0   
...                 ...                 ...                ...   
ZEPH                  0                   0                  0   
GAP                   1                   0                  0   
BDX                   0                   0                  0   
ZEN                   0                   0                  0   
XBC                   0                   0                  0   

      ProofType_PoW/nPoS  ProofType_Pos  ProofType_Proof of Authority  \
42                     0              0                             0   
404                    0              0                             0   
1337                   0              0                             0   
BTC                    0              0                             0   
ETH                    0              0                             0   
...                  ...            ...                           ...   
ZEPH                   0              0                             0   
GAP                    0              0                             0   
BDX                    0              0                  

In [14]:
# Standardize the data with StandardScaler().
x_scaled = StandardScaler().fit_transform(x)
print(x_scaled)

[[-0.11674788 -0.15286468 -0.0433555  ... -0.0433555  -0.0433555
  -0.0433555 ]
 [-0.09358885 -0.14499604 -0.0433555  ... -0.0433555  -0.0433555
  -0.0433555 ]
 [ 0.52587231  4.4937636  -0.0433555  ... -0.0433555  -0.0433555
  -0.0433555 ]
 ...
 [-0.09523411 -0.13215444 -0.0433555  ... -0.0433555  -0.0433555
  -0.0433555 ]
 [-0.11658774 -0.15255408 -0.0433555  ... -0.0433555  -0.0433555
  -0.0433555 ]
 [-0.11674507 -0.15284989 -0.0433555  ... -0.0433555  -0.0433555
  -0.0433555 ]]


### Deliverable 2: Reducing Data Dimensions Using PCA

In [62]:
# Using PCA to reduce dimension to three principal components.
n_comp = 3
pca = PCA(n_components=n_comp)
x_pca = pca.fit_transform(x_scaled)
x_pca

array([[-0.33393975,  0.94231413, -0.60875295],
       [-0.31729932,  0.94254946, -0.60915973],
       [ 2.29439355,  1.67367318, -0.68698606],
       ...,
       [ 0.31738532, -2.33259924,  0.43295104],
       [-0.14152886, -1.81766482,  0.40707484],
       [-0.28495414,  0.79850191, -0.2918048 ]])

In [64]:
# Create a DataFrame with the three principal components.
col_names = [f"PC {i}" for i in range(1, n_comp + 1)]
pcs_df = pd.DataFrame(x_pca, columns=col_names, index=cleaned_crypto_df.index)
print(pcs_df.shape)
pcs_df.head(10)

(533, 3)


PC 1      PC 2      PC 3
42   -0.333940  0.942314 -0.608753
404  -0.317299  0.942549 -0.609160
1337  2.294394  1.673673 -0.686986
BTC  -0.146166 -1.290000  0.236839
ETH  -0.148550 -1.996065  0.422144
LTC  -0.160698 -1.182415 -0.010559
DASH -0.404785  1.235275 -0.541306
XMR  -0.151070 -2.192462  0.416457
ETC  -0.146995 -1.996156  0.422130
ZEC  -0.141528 -1.817665  0.407075

In [56]:

df_x_pca.set_index('index')
df_x_pca.head()

PC 1      PC 2      PC 3 index
0 -0.330758  1.029064 -0.616756    42
1 -0.314082  1.029140 -0.617329   404
2  2.307520  1.601463 -0.696088  1337
3 -0.142232 -1.335685  0.249111   BTC
4 -0.149974 -2.021221  0.437273   ETH

### Deliverable 3: Clustering Crytocurrencies Using K-Means

#### Finding the Best Value for `k` Using the Elbow Curve

In [54]:
# Create an elbow curve to find the best value for K.
# YOUR CODE HERE


Running K-Means with `k=4`

In [15]:
# Initialize the K-Means model.
# YOUR CODE HERE

# Fit the model
# YOUR CODE HERE

# Predict clusters
# YOUR CODE HERE

array([0, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1,
       1, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0,
       1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1,
       1, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0,
       0, 1, 0, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1,
       0, 1, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0,
       1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0,
       0, 1, 1, 1, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0,
       0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0,
       1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0,
       0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0,
       0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0,
       0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1,
       0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 0,

In [16]:
# Create a new DataFrame including predicted clusters and cryptocurrencies features.
# Concatentate the crypto_df and pcs_df DataFrames on the same columns.
# YOUR CODE HERE

#  Add a new column, "CoinName" to the clustered_df DataFrame that holds the names of the cryptocurrencies. 
# YOUR CODE HERE

#  Add a new column, "Class" to the clustered_df DataFrame that holds the predictions.
# YOUR CODE HERE

# Print the shape of the clustered_df
print(clustered_df.shape)
clustered_df.head(10)

(532, 9)


Algorithm ProofType  TotalCoinsMined TotalCoinSupply      PC 1  \
42            Scrypt   PoW/PoS     4.199995e+01              42 -0.332855   
404           Scrypt   PoW/PoS     1.055185e+09       532000000 -0.316201   
1337             X13   PoW/PoS     2.927942e+10    314159265359  2.300040   
BTC          SHA-256       PoW     1.792718e+07        21000000 -0.149023   
ETH           Ethash       PoW     1.076842e+08               0 -0.162646   
LTC           Scrypt       PoW     6.303924e+07        84000000 -0.159391   
DASH             X11   PoW/PoS     9.031294e+06        22000000 -0.410793   
XMR   CryptoNight-V7       PoW     1.720114e+07               0 -0.148242   
ETC           Ethash       PoW     1.133597e+08       210000000 -0.161087   
ZEC         Equihash       PoW     7.383056e+06        21000000 -0.179011   

          PC 2      PC 3          CoinName  Class  
42    1.038358 -0.564944           42 Coin      0  
404   1.038515 -0.565371           404Coin      0  
1337  1.643532 -0.570651         EliteCoin      0  
BTC  -1.309646  0.182620           Bitcoin      1  
ETH  -2.019908  0.380155          Ethereum      1  
LTC  -1.123165 -0.021041          Litecoin      1  
DASH  1.224033 -0.517184              Dash      0  
XMR  -2.196597  0.375973            Monero      1  
ETC  -2.020010  0.380143  Ethereum Classic      1  
ZEC  -2.024700  0.433256             ZCash      1

### Deliverable 4: Visualizing Cryptocurrencies Results

#### 3D-Scatter with Clusters

In [17]:
# Creating a 3D-Scatter with the PCA data and the clusters
# YOUR CODE HERE


In [18]:
# Create a table with tradable cryptocurrencies.
# YOUR CODE HERE

:Table   [CoinName,Algorithm,ProofType,TotalCoinSupply,TotalCoinsMined,Class]

In [19]:
# Print the total number of tradable cryptocurrencies.
# YOUR CODE HERE

There are 532 tradable cryptocurrencies.


In [20]:
# Scaling data to create the scatter plot with tradable cryptocurrencies.
# YOUR CODE HERE

array([[4.20000000e-11, 0.00000000e+00],
       [5.32000000e-04, 1.06585544e-03],
       [3.14159265e-01, 2.95755135e-02],
       ...,
       [1.40022261e-03, 9.90135079e-04],
       [2.10000000e-05, 7.37028150e-06],
       [1.00000000e-06, 1.29582282e-07]])

In [21]:
# Create a new DataFrame that has the scaled data with the clustered_df DataFrame index.
# YOUR CODE HERE

# Add the "CoinName" column from the clustered_df DataFrame to the new DataFrame.
# YOUR CODE HERE

# Add the "Class" column from the clustered_df DataFrame to the new DataFrame. 
# YOUR CODE HERE

plot_df.head(10)

TotalCoinSupply  TotalCoinsMined          CoinName  Class
42       4.200000e-11         0.000000           42 Coin      0
404      5.320000e-04         0.001066           404Coin      0
1337     3.141593e-01         0.029576         EliteCoin      0
BTC      2.100000e-05         0.000018           Bitcoin      1
ETH      0.000000e+00         0.000109          Ethereum      1
LTC      8.400000e-05         0.000064          Litecoin      1
DASH     2.200000e-05         0.000009              Dash      0
XMR      0.000000e+00         0.000017            Monero      1
ETC      2.100000e-04         0.000115  Ethereum Classic      1
ZEC      2.100000e-05         0.000007             ZCash      1

In [22]:
# Create a hvplot.scatter plot using x="TotalCoinsMined" and y="TotalCoinSupply".
# YOUR CODE HERE


:NdOverlay   [Class]
   :Scatter   [TotalCoinsMined]   (TotalCoinSupply,CoinName)